# Yellow Diamond iPython/Jupyter Notebook

## Step 1: Run Cell 1 to define `readIntensity` function

`readIntensity`
* Expects: String, name of file containing columns of data
    * Column 1 must contain $\lambda$ in nm
    * Column 2 must contain $I(\lambda)/I_0(\lambda)$
* Returns: 2-tuple containing read-in list of $\lambda$ and read-in list of $I(\lambda)$

In [1]:
def readIntensity(file):
    wavelengths = []
    I = []
    for line in open(file, 'r'):
        cols = (line.strip()).split()
        wavelengths.append(float(cols[0]))
        I.append(float(cols[1]))
    return wavelengths, I

## Step 2: Run Cell 2 to define `interpolatedSpectrum` function

`interpolatedSpectrum`
* Expects: 2-tuple containing read-in list of $\lambda$ and read-in list of $I(\lambda)$
* Optional: Specify illuminant
    * "D65"
    * Uniform (default)
* Returns: ColorPy spectrum object with linear interpolation of intensity spectrum.
    * Values outside give $\lambda$ range are set to 0

In [2]:
def interpolatedSpectrum((wavelengths, I), illuminant=None):
    from colorpy import ciexyz, illuminants
    import numpy as np
    from scipy import interpolate
    
    # Define linear interpolation of given I with values outside of data range set to zero
    f = interpolate.interp1d(wavelengths, I, bounds_error=False, fill_value=0.0)
    
    # Fill and empty spectrum object with interpolated intensities
    spectrum = ciexyz.empty_spectrum()
    # Get list of I at wavelengths from spectrum
    interpolatedIntensities = f(spectrum.transpose()[0])
    
    # Define incident light
    if illuminant is "D65":
        incident = illuminants.get_illuminant_D65()
    else:
        incident = illuminants.get_constant_illuminant()
    
    # Scale the relative/interpolated intensities by the chosen illuminant
    (num_rows, num_cols) = spectrum.shape
    for i in xrange(num_rows):
        spectrum[i][1] = incident[i][1] * interpolatedIntensities[i]
    
    return spectrum

## Step 3: Run Cell 3 to generate plots
Make sure to define these:
* `datafolder`: where the input intensity data files are located
* `plotfolder`: where the output plots will be saved
* `structures`: list of structure labels
    * Input files expected to be of form [structure]_final.dat
* `illuminants`: list of illuminants to use with `interpolatedSpectrum` function

In [15]:
import colorpy
from IPython import display

datafolder = "5-nm-data/"
plotfolder = "plots/"

structures = ["N0V0", "N0V1", "N1V0", "N1V1", "N2V0", "N2V1", "N3V1", "N4V1"]
illuminants = ["D65", "Uniform"]

xaxis = "Wavelength (nm)"
yaxis = "Intensity (W/m^2)"

for ill in illuminants:
    for struct in structures:
        datafile = datafolder + struct + "_final.dat"
        plotfile = plotfolder + ill + "-" + struct
        plottitle = " ".join([struct, "using", ill])
    
        spectrum = interpolatedSpectrum(readIntensity(datafile), illuminant=ill)
        colorpy.plots.spectrum_plot(spectrum, plottitle, plotfile, xaxis, yaxis)

Saving plot plots/D65-N0V0
Saving plot plots/D65-N0V1
Saving plot plots/D65-N1V0
Saving plot plots/D65-N1V1
Saving plot plots/D65-N2V0
Saving plot plots/D65-N2V1
Saving plot plots/D65-N3V1
Saving plot plots/D65-N4V1
Saving plot plots/Uniform-N0V0
Saving plot plots/Uniform-N0V1
Saving plot plots/Uniform-N1V0
Saving plot plots/Uniform-N1V1
Saving plot plots/Uniform-N2V0
Saving plot plots/Uniform-N2V1
Saving plot plots/Uniform-N3V1
Saving plot plots/Uniform-N4V1
